In [1]:
%%capture --no-stderr
%pip install --quiet -U langgraph langchain-core langchain_openai python-dotenv langsmith pydantic spotipy tenacity

In [2]:
%pip install --quiet -U jupyterlab-lsp
%pip install --quiet -U "python-lsp-server[all]"

Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


In [3]:
## Setup logging
import logging
import os
from dotenv import load_dotenv

load_dotenv(override=True)
logger = logging.getLogger(__name__)

# Configure logging
logging.basicConfig(
    level=logging.INFO,
    format='%(asctime)s - %(levelname)s - %(message)s',  # Define the format
    handlers=[logging.StreamHandler()]  # Output to the console
)

# Define Search Tool

In [4]:
from langchain_community.tools.tavily_search import TavilySearchResults

search_tool = TavilySearchResults(
    max_results=50,
    include_answer=True,
    include_raw_content=True,
    include_images=True,
    # search_depth="advanced",
    # include_domains = []
    # exclude_domains = []
)
name = search_tool.get_name()
desc = search_tool.description
desc

'A search engine optimized for comprehensive, accurate, and trusted results. Useful for when you need to answer questions about current events. Input should be a search query.'

# Create ToolNode

In [ ]:
from langgraph.prebuilt import ToolNode
from spotify_tools import get_playlists, create_spotify_playlist, add_tracks_to_playlist, filter_artists, get_artists_from_playlist, find_similar_artists, find_top_tracks, get_audio_features
from plan import validate_plan

tools = [get_playlists, create_spotify_playlist, add_tracks_to_playlist, filter_artists, validate_plan, get_artists_from_playlist, find_similar_artists, find_top_tracks, search_tool, get_audio_features]
tool_node = ToolNode(tools)

# Bind Tools to Model

In [6]:
from langchain_openai import ChatOpenAI

llm = ChatOpenAI(model=os.getenv("OPENAI_MODEL_NAME"), temperature=1.0)
# llm_with_tools = llm.bind_tools(tools, strict=True, parallel_tool_calls=False)
llm_with_tools = llm.bind_tools(tools, strict=True)

# System Prompt

In [7]:
from langchain_core.messages import SystemMessage
from prompts import Prompts

system_message = SystemMessage(Prompts.SYSTEM)


# First Message

In [ ]:
from langchain_core.messages import HumanMessage
from prompts import Prompts

human_message = HumanMessage(Prompts.SPOTIFY)
llm_response = llm_with_tools.invoke([system_message, human_message])

2024-11-26 10:10:34,474 - INFO - HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"


In [ ]:
if llm_response.tool_calls is None or llm_response.tool_calls[0]["name"] != "validate_plan":
    raise ValueError("should be tool message calling 'validate_plan'")

In [12]:
llm_response.pretty_print()

================================== Ai Message ==================================
Tool Calls:
  validate_plan (call_ub32PQwDou5iBexyjUGvYzdb)
 Call ID: call_ub32PQwDou5iBexyjUGvYzdb
  Args:
    plan: {'steps': [{'step_number': 1, 'name': 'get-original-playlist-artists', 'type': 'action', 'description': "Retrieve all artists from the 'New Rock and Blues' playlist.", 'success_criteria': "A list of unique artist IDs from the playlist 'New Rock and Blues'.", 'tool': 'functions.get_artists_from_playlist', 'action': "Get the list of unique artists from 'New Rock and Blues' playlist.", 'condition': None, 'substeps': None}, {'step_number': 2, 'name': 'find-similar-artists-loop', 'type': 'loop', 'description': 'For each artist retrieved in the previous step, find 3-4 artists of similar style.', 'success_criteria': 'A list of similar artists for each original artist gathered.', 'tool': 'functions.find_similar_artists', 'action': 'Find similar artists', 'condition': 'For each artist in the origina

In [13]:
plan = llm_response.tool_calls[0]["args"]
plan

{'plan': {'steps': [{'step_number': 1,
    'name': 'get-original-playlist-artists',
    'type': 'action',
    'description': "Retrieve all artists from the 'New Rock and Blues' playlist.",
    'success_criteria': "A list of unique artist IDs from the playlist 'New Rock and Blues'.",
    'tool': 'functions.get_artists_from_playlist',
    'action': "Get the list of unique artists from 'New Rock and Blues' playlist.",
    'condition': None,
    'substeps': None},
   {'step_number': 2,
    'name': 'find-similar-artists-loop',
    'type': 'loop',
    'description': 'For each artist retrieved in the previous step, find 3-4 artists of similar style.',
    'success_criteria': 'A list of similar artists for each original artist gathered.',
    'tool': 'functions.find_similar_artists',
    'action': 'Find similar artists',
    'condition': 'For each artist in the original list',
    'substeps': [{'step_number': 1,
      'name': 'find-similar-artists',
      'type': 'action',
      'description':

# chat_prompt_template holds all messages (Human, AI, Tool)

In [14]:
from langchain_core.prompts import ChatPromptTemplate

chat_prompt_template: ChatPromptTemplate = system_message + human_message + llm_response
messages = chat_prompt_template.format_messages()
messages

[SystemMessage(content="\n    You are an AI language assistant designed to execute tasks with precision and attention to detail. Your primary objective is to follow the user's instructions thoroughly and exactly as specified, leaving no detail unaddressed.\n\n    Guidelines:\n\n    - **Carefully Read Instructions:** Before starting any task, read all user instructions thoroughly to ensure complete understanding.\n\n    - **Create a Detailed Plan:** Develop a step-by-step plan that addresses every aspect of the user's requirements. Validate this plan before execution.\n\n    - **Utilize Advanced Planning Structures:** Do not limit yourself to linear or sequential plans. Employ loops for repetitive tasks, branches for conditional logic, and other programming constructs to handle complex tasks and decision-making processes.\n\n    - **Follow Instructions Precisely:** Execute each step exactly as described, without omitting or altering any part of the instructions.\n\n    - **Be Thorough:*

# Check for Tools in Message

In [ ]:
from typing import Any, Callable, List
from langchain_core.messages import BaseMessage

def check_tool_in_messages(messages: List[BaseMessage], tools: List[Callable[..., Any]]) -> List[str]:
    tools_in_ai_message = []
    tools_by_name = {tool.name: tool for tool in tools}
    for tool_call in messages[-1].tool_calls:
        tool = tools_by_name[tool_call["name"]]
        tools_in_ai_message.append(tool)
        # observation = tool.invoke(tool_call["args"])
        # result.append(ToolMessage(content=observation, tool_call_id=tool_call["id"]))
    return tools_in_ai_message

# Tool Call (should be validate_plan())

In [15]:
tool_response = tool_node.invoke({"messages": messages})
tool_message = tool_response["messages"][0]
tool_message.pretty_print()

================================= Tool Message =================================
Name: validate_plan

true


# Add Tool Response to Messages

In [16]:
chat_prompt_template += tool_message
chat_prompt_template.format_messages()

[SystemMessage(content="\n    You are an AI language assistant designed to execute tasks with precision and attention to detail. Your primary objective is to follow the user's instructions thoroughly and exactly as specified, leaving no detail unaddressed.\n\n    Guidelines:\n\n    - **Carefully Read Instructions:** Before starting any task, read all user instructions thoroughly to ensure complete understanding.\n\n    - **Create a Detailed Plan:** Develop a step-by-step plan that addresses every aspect of the user's requirements. Validate this plan before execution.\n\n    - **Utilize Advanced Planning Structures:** Do not limit yourself to linear or sequential plans. Employ loops for repetitive tasks, branches for conditional logic, and other programming constructs to handle complex tasks and decision-making processes.\n\n    - **Follow Instructions Precisely:** Execute each step exactly as described, without omitting or altering any part of the instructions.\n\n    - **Be Thorough:*

# Send Messages with Tool result to LLM

In [17]:
llm_response = llm_with_tools.invoke(chat_prompt_template.format_messages())
llm_response.pretty_print()

2024-11-26 10:11:23,484 - INFO - HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"


================================== Ai Message ==================================
Tool Calls:
  get_playlists (call_R3Ik0D08IJku8TlDdobCGu6T)
 Call ID: call_R3Ik0D08IJku8TlDdobCGu6T
  Args:


# Validate correct tool call

In [ ]:
if llm_response.tool_calls is None or llm_response.tool_calls[0]["name"] != "get_playlists":
    raise ValueError("should be tool message calling 'validate_plan'")

# Tool Call (should be get_playlists())

In [18]:
chat_prompt_template += llm_response
messages = chat_prompt_template.format_messages()
tool_response = tool_node.invoke({"messages": messages})

In [19]:
for tool_message in tool_response["messages"]:
    tool_message.pretty_print()

================================= Tool Message =================================
Name: get_playlists

[{"id": "3IidWsefzg2r1zA8gg8lUi", "name": "Modern Rock Vibes"}, {"id": "34Y803AoVL4ceg6jKNN2cz", "name": "Modern Rock and Blues Vibes"}, {"id": "2dbYK5b7J0F7IdH5n1TEUK", "name": "RPreacher"}, {"id": "4ack9YtUhdxRayJDAqlfQe", "name": "RP Bossa Nova Chill "}, {"id": "75NW18NgdZuZeifrcjxKlZ", "name": "GVF"}, {"id": "5iyONtUO21O88xw8pBblwh", "name": "Now And Then"}, {"id": "4SDSUMg2HJcGFmHlupsU7U", "name": "Jazz classics"}, {"id": "5fBxLG2wLAPVpx83402rHl", "name": "Acdc"}, {"id": "17Yxm5hQbkbZwDcCTuiDXC", "name": "einaudi"}, {"id": "2X6GccWfIqPWO6VYx405nO", "name": "Eric Clapton Blues"}, {"id": "3smVXe8y8w8nt4lFH0HBkW", "name": "Alchemy: Dire Straits"}, {"id": "2ifRZBXnX7UmIPUlGet5WZ", "name": "Blues"}, {"id": "5nn2ePtd9gYEEDL3XnACCB", "name": "brazil"}, {"id": "6YAntoKNXuogPKdV26b6XE", "name": "CCR"}, {"id": "2VHkZvOMCkLF3B7TsKerKD", "name": "Chill"}, {"id": "508lbLx9XUkHv5Xb45hxTP", "nam

# Add Tool Response to Messages

In [20]:
chat_prompt_template += tool_response["messages"]
messages = chat_prompt_template.format_messages()
messages

[SystemMessage(content="\n    You are an AI language assistant designed to execute tasks with precision and attention to detail. Your primary objective is to follow the user's instructions thoroughly and exactly as specified, leaving no detail unaddressed.\n\n    Guidelines:\n\n    - **Carefully Read Instructions:** Before starting any task, read all user instructions thoroughly to ensure complete understanding.\n\n    - **Create a Detailed Plan:** Develop a step-by-step plan that addresses every aspect of the user's requirements. Validate this plan before execution.\n\n    - **Utilize Advanced Planning Structures:** Do not limit yourself to linear or sequential plans. Employ loops for repetitive tasks, branches for conditional logic, and other programming constructs to handle complex tasks and decision-making processes.\n\n    - **Follow Instructions Precisely:** Execute each step exactly as described, without omitting or altering any part of the instructions.\n\n    - **Be Thorough:*

# Send Tool Result Results to LLM

In [21]:
llm_response = llm_with_tools.invoke(messages)
llm_response.pretty_print()

2024-11-26 10:11:45,666 - INFO - HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"


================================== Ai Message ==================================
Tool Calls:
  get_artists_from_playlist (call_i6l4iZPc7jvYOcfkK48nqYpj)
 Call ID: call_i6l4iZPc7jvYOcfkK48nqYpj
  Args:
    playlist_id: 01tk0aitEuGK0ajWCkzdKc


# Validate correct tool call

In [ ]:
if llm_response.tool_calls is None or llm_response.tool_calls[0]["name"] != "get_artists_from_playlist":
    raise ValueError("should be tool message calling 'get_artists_from_playlist'")

# Add AI Tool Call to Messages

In [22]:
chat_prompt_template += llm_response
messages = chat_prompt_template.format_messages()

# Tool Call (get_artists_from_playlist())

In [23]:
tool_response = tool_node.invoke({"messages": messages})
for tool_message in tool_response["messages"]:
    tool_message.pretty_print()

================================= Tool Message =================================
Name: get_artists_from_playlist

{"01aC2ikO4Xgb2LUpf9JfKp": "Gary Clark Jr.", "1iEaqWaYpKo9x0OrEq7Q7z": "Ayron Jones", "0RqtSIYZmd4fiBKVFqyIqD": "Thirty Seconds To Mars", "7jdFEYD2LTYjfwxOdlVjmc": "KALEO", "7Ln80lUS6He07XvHI8qqHH": "Arctic Monkeys", "4pejUc4iciQfgdX6OKulQn": "Queens of the Stone Age", "0Nrwy16xCPXG8AwkMbcVvo": "Black Pistol Fire", "1xKrH6GSh9CJh8nYwbqW7B": "Welshly Arms", "6vYg01ZFt1nREsUDMDPUYX": "The Record Company", "0bZCak2tcRMY1dzEIuwF42": "The Heavy", "4NpFxQe2UvRCAjto3JqlSl": "Greta Van Fleet", "26opZSJcXshCmCwxgZQmBc": "Whiskey Myers", "3xYXYzm9H3RzyQgBrYwIcx": "Colter Wall", "13ZEDW6vyBF12HYcZRr4EV": "Tyler Childers", "4YLtscXsxbVgi031ovDDdh": "Chris Stapleton", "5VPCIIfZPK8KPsgz4jmOEC": "The Blue Stones", "1l9I7G8J8AnMScWQwlNJ4M": "Goodbye June", "12Chz98pHFMPJEknJQMWvI": "Muse", "5HsS48kuvghKcNpwOaAvB5": "Samantha Fish", "7mnBLXK823vNxN3UWB7Gfz": "The Black Keys", "3mVWMgLc7bcyC

# Add Tool Response to Messages

In [24]:
chat_prompt_template += tool_response["messages"]
messages = chat_prompt_template.format_messages()
messages

[SystemMessage(content="\n    You are an AI language assistant designed to execute tasks with precision and attention to detail. Your primary objective is to follow the user's instructions thoroughly and exactly as specified, leaving no detail unaddressed.\n\n    Guidelines:\n\n    - **Carefully Read Instructions:** Before starting any task, read all user instructions thoroughly to ensure complete understanding.\n\n    - **Create a Detailed Plan:** Develop a step-by-step plan that addresses every aspect of the user's requirements. Validate this plan before execution.\n\n    - **Utilize Advanced Planning Structures:** Do not limit yourself to linear or sequential plans. Employ loops for repetitive tasks, branches for conditional logic, and other programming constructs to handle complex tasks and decision-making processes.\n\n    - **Follow Instructions Precisely:** Execute each step exactly as described, without omitting or altering any part of the instructions.\n\n    - **Be Thorough:*

# Send Tool Result to LLM

In [25]:
llm_response = llm_with_tools.invoke(messages)
llm_response.pretty_print()

2024-11-26 10:12:30,494 - INFO - HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"


================================== Ai Message ==================================
Tool Calls:
  find_similar_artists (call_ZsqjqasnppYGQ6GfK0SE2oJZ)
 Call ID: call_ZsqjqasnppYGQ6GfK0SE2oJZ
  Args:
    artists: ['01aC2ikO4Xgb2LUpf9JfKp', '1iEaqWaYpKo9x0OrEq7Q7z', '0RqtSIYZmd4fiBKVFqyIqD', '7jdFEYD2LTYjfwxOdlVjmc', '7Ln80lUS6He07XvHI8qqHH', '4pejUc4iciQfgdX6OKulQn', '0Nrwy16xCPXG8AwkMbcVvo', '1xKrH6GSh9CJh8nYwbqW7B', '6vYg01ZFt1nREsUDMDPUYX', '0bZCak2tcRMY1dzEIuwF42']
  find_similar_artists (call_1gzYPlMxtJqciqf5d3SyFD3j)
 Call ID: call_1gzYPlMxtJqciqf5d3SyFD3j
  Args:
    artists: ['4NpFxQe2UvRCAjto3JqlSl', '26opZSJcXshCmCwxgZQmBc', '3xYXYzm9H3RzyQgBrYwIcx', '13ZEDW6vyBF12HYcZRr4EV', '4YLtscXsxbVgi031ovDDdh', '5VPCIIfZPK8KPsgz4jmOEC', '1l9I7G8J8AnMScWQwlNJ4M', '12Chz98pHFMPJEknJQMWvI', '5HsS48kuvghKcNpwOaAvB5', '7mnBLXK823vNxN3UWB7Gfz']
  find_similar_artists (call_bttz6ovsIG7YJTpNYFXpztgk)
 Call ID: call_bttz6ovsIG7YJTpNYFXpztgk
  Args:
    artists: ['3mVWMgLc7bcyCBtL2ymZwK', '2ziB7fzrX

# Check Tool Call

In [ ]:
if llm_response.tool_calls is None or llm_response.tool_calls[0]["name"] != "find_similar_artists":
    raise ValueError("should be tool message calling 'find_similar_artists'")

# Add AI Tool Call to Messages

In [26]:
chat_prompt_template += llm_response
messages = chat_prompt_template.format_messages()
messages

[SystemMessage(content="\n    You are an AI language assistant designed to execute tasks with precision and attention to detail. Your primary objective is to follow the user's instructions thoroughly and exactly as specified, leaving no detail unaddressed.\n\n    Guidelines:\n\n    - **Carefully Read Instructions:** Before starting any task, read all user instructions thoroughly to ensure complete understanding.\n\n    - **Create a Detailed Plan:** Develop a step-by-step plan that addresses every aspect of the user's requirements. Validate this plan before execution.\n\n    - **Utilize Advanced Planning Structures:** Do not limit yourself to linear or sequential plans. Employ loops for repetitive tasks, branches for conditional logic, and other programming constructs to handle complex tasks and decision-making processes.\n\n    - **Follow Instructions Precisely:** Execute each step exactly as described, without omitting or altering any part of the instructions.\n\n    - **Be Thorough:*

# Tool Call (find_similar_artists())

In [27]:
tool_response = tool_node.invoke({"messages": messages})
for tool_message in  tool_response["messages"]:
    tool_message.pretty_print()

================================= Tool Message =================================
Name: find_similar_artists

{"02seUFsFQP7TH4hLrTj77o": "Nathaniel Rateliff & The Night Sweats", "4fXkvh05wFhuH77MfD4m9o": "St. Paul & The Broken Bones", "5kuJibJcwOC53s3OkoGMRA": "The Revivalists", "7mnBLXK823vNxN3UWB7Gfz": "The Black Keys", "0tgaHqkU1p7QhBUIzKXVU9": "The Marcus King Band", "1Jl8u1U1GtBlwocZK5LWZv": "JJ Grey & Mofro", "356c8AN5YWKvz86B4Sb1yf": "Rival Sons", "521Jw1ixgckc0WJHhm2Klu": "Quaker City Night Hawks", "4xac3zhHlBm5QDxbZeqgeR": "Robert Randolph & The Family Band", "1riHqX633Kup3mJAw8WR8p": "Kenny Wayne Shepherd", "6YWdHD3R863Apw1hkx3BwC": "Dan Auerbach", "5krkohEVJYw0qoB5VWwxaC": "The Black Crowes", "40N10exWtaCVUtBMftQn3t": "The Stone Foxes", "16GcWuvvybAoaHr0NqT8Eh": "Alabama Shakes", "5fsDcuclIe8ZiBD5P787K1": "Stevie Ray Vaughan", "2gFsmDBM0hkoZPmrO5EdyO": "Tedeschi Trucks Band", "5rX1EodZfwxmW4fQX2Caot": "Jonny Lang", "5jMGnqJkgPaiJzwy5bOcYX": "Christone \"Kingfish\" Ingram", "6

# Add Tool Response to Messages

In [28]:
chat_prompt_template += tool_response["messages"]
messages = chat_prompt_template.format_messages()
messages

[SystemMessage(content="\n    You are an AI language assistant designed to execute tasks with precision and attention to detail. Your primary objective is to follow the user's instructions thoroughly and exactly as specified, leaving no detail unaddressed.\n\n    Guidelines:\n\n    - **Carefully Read Instructions:** Before starting any task, read all user instructions thoroughly to ensure complete understanding.\n\n    - **Create a Detailed Plan:** Develop a step-by-step plan that addresses every aspect of the user's requirements. Validate this plan before execution.\n\n    - **Utilize Advanced Planning Structures:** Do not limit yourself to linear or sequential plans. Employ loops for repetitive tasks, branches for conditional logic, and other programming constructs to handle complex tasks and decision-making processes.\n\n    - **Follow Instructions Precisely:** Execute each step exactly as described, without omitting or altering any part of the instructions.\n\n    - **Be Thorough:*

# Send Tool Result to LLM

In [29]:
llm_response = llm_with_tools.invoke(messages)
llm_response.pretty_print()

2024-11-26 10:13:54,805 - INFO - HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"


================================== Ai Message ==================================
Tool Calls:
  filter_artists (call_bECdnTwJHXgEJNT0uWPkq6UV)
 Call ID: call_bECdnTwJHXgEJNT0uWPkq6UV
  Args:
    playlist_id: 01tk0aitEuGK0ajWCkzdKc
    new_artists: ['02seUFsFQP7TH4hLrTj77o', '1Jl8u1U1GtBlwocZK5LWZv', '02uYdhMhCgdB49hZlYRm9o', '0bZCak2tcRMY1dzEIuwF42', '01aC2ikO4Xgb2LUpf9JfKp', '0RqtSIYZmd4fiBKVFqyIqD', '521Jw1ixgckc0WJHhm2Klu', '5tFRohaO5yEsuJxmMnlCO9', '0tgaHqkU1p7QhBUIzKXVU9', '6VDdCwrBM4qQaGxoAyxyJC', '36QJpDe2go2KgaRleHCDTp', '0XNa1vTidXlvJ2gHSsRi4A', '7mnBLXK823vNxN3UWB7Gfz', '1Ffb6ejR6Fe5IamqA5oRUF', '56ZTgzPBDge0OvCGgMO3OY', '0nrWy16xCPXG8AwkMbcVv0', '22bE4uQ6baNwSHPVcDxLCe', '5I4eibDkC6kQps3o8qr3Ef', '7C82Bw5AiySQQHfwDvcP9e', '4icMtMWg5th8cdLzXW7WY5', '66YGDwn22fjphzqGCSIbbK', '1iEaqWaYpKo9x0OrEq7Q7z', '6yJCxee7QumYr820xdIsjo', '00FQb4jTyendYWaN8pK0wa', '5u5A31mF4lQSoPEiafsW4r', '0C0XlULifJtAgn6ZNCW2eu', '3lzTSpBz7pJHWQU5i3zaP1', '7vg2TnAXwg4cMnsqsG7a0n', '0Nrwy16xCPXG8AwkMbcVvo'

# Add AI Tool Call to Messages

In [30]:
chat_prompt_template += llm_response
messages = chat_prompt_template.format_messages()
messages

[SystemMessage(content="\n    You are an AI language assistant designed to execute tasks with precision and attention to detail. Your primary objective is to follow the user's instructions thoroughly and exactly as specified, leaving no detail unaddressed.\n\n    Guidelines:\n\n    - **Carefully Read Instructions:** Before starting any task, read all user instructions thoroughly to ensure complete understanding.\n\n    - **Create a Detailed Plan:** Develop a step-by-step plan that addresses every aspect of the user's requirements. Validate this plan before execution.\n\n    - **Utilize Advanced Planning Structures:** Do not limit yourself to linear or sequential plans. Employ loops for repetitive tasks, branches for conditional logic, and other programming constructs to handle complex tasks and decision-making processes.\n\n    - **Follow Instructions Precisely:** Execute each step exactly as described, without omitting or altering any part of the instructions.\n\n    - **Be Thorough:*

# Tool Call (filter_artists())

In [31]:
tool_response = tool_node.invoke({"messages": messages})
for tool_message in  tool_response["messages"]:
    tool_message.pretty_print()

================================= Tool Message =================================
Name: filter_artists

{'7eEcNkh8fOLBbnNjq1Li8j', '2ti8H0pCANj5EgRj4FkoPW', '1Jl8u1U1GtBlwocZK5LWZv', '57Z3wNX4savyPPeFxHKoIt', '6VNktN7R1JVp8P4IkePTyX', '3XLlREMeBNOsm0wGSB8yC3', '02uYdhMhCgdB49hZlYRm9o', '7vg2TnAXwg4cMnsqsG7a0n', '5yu0c5TSXhGjKX5NtsgItO', '0UJIPs8Nsz6Y2P5g5DyRTu', '3RCQGsx8bTx6o7SrFGksCo', '7mFI2ZpF8IVcr0zQFBXxka', '00FQb4jTyendYWaN8pK0wa', '305frv0D0vth3wrdlzXXuM', '7rv4vIcU3eHC5qOH1F3KL7', '0tgaHqkU1p7QhBUIzKXVU9', '0z4suz8TQLBcClNueTMRay', '5B5JuBzVwvYU167uS0WMCt', '0nrWy16xCPXG8AwkMbcVv0', '2Yhge9XMasL2pMlIkJeД0z', '5I4eibDkC6kQps3o8qr3Ef', '02seUFsFQP7TH4hLrTj77o', '4tNl5VOwm6g8QjqKgomH2z', '6bVGvVU0tNgV7QtRk4QLIL', '521Jw1ixgckc0WJHhm2Klu', '4icMtMWg5th8cdLzXW7WY5', '1SH6uqCGEoVR6REHLbZbHj', '6X5G9rF7yPhnLki5tElX5z', '0C0XlULifJtAgn6ZNCW2eu', '56ZTgzPBDge0OvCGgMO3OY', '2YtupCfK9pMQpJ9AQ0ypgU', '4b2IDegUo1YT9kgXveBqRj', '7C82Bw5AiySQQHfwDvcP9e', '36QJpDe2go2KgaRleHCDTp', '6k8jtB1ZrdR

# Add Tool Response to Messages

In [32]:
chat_prompt_template += tool_response["messages"]
messages = chat_prompt_template.format_messages()
messages

[SystemMessage(content="\n    You are an AI language assistant designed to execute tasks with precision and attention to detail. Your primary objective is to follow the user's instructions thoroughly and exactly as specified, leaving no detail unaddressed.\n\n    Guidelines:\n\n    - **Carefully Read Instructions:** Before starting any task, read all user instructions thoroughly to ensure complete understanding.\n\n    - **Create a Detailed Plan:** Develop a step-by-step plan that addresses every aspect of the user's requirements. Validate this plan before execution.\n\n    - **Utilize Advanced Planning Structures:** Do not limit yourself to linear or sequential plans. Employ loops for repetitive tasks, branches for conditional logic, and other programming constructs to handle complex tasks and decision-making processes.\n\n    - **Follow Instructions Precisely:** Execute each step exactly as described, without omitting or altering any part of the instructions.\n\n    - **Be Thorough:*

# Send Tool Result to LLM

In [33]:
llm_response = llm_with_tools.invoke(messages)
llm_response.pretty_print()

2024-11-26 10:15:47,302 - INFO - HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"


================================== Ai Message ==================================
Tool Calls:
  tavily_search_results_json (call_gjvKgrED2Zd5xiiA5mdWNDVF)
 Call ID: call_gjvKgrED2Zd5xiiA5mdWNDVF
  Args:
    query: music artist success after 2010


In [34]:
chat_prompt_template += llm_response
messages = chat_prompt_template.format_messages()
messages

[SystemMessage(content="\n    You are an AI language assistant designed to execute tasks with precision and attention to detail. Your primary objective is to follow the user's instructions thoroughly and exactly as specified, leaving no detail unaddressed.\n\n    Guidelines:\n\n    - **Carefully Read Instructions:** Before starting any task, read all user instructions thoroughly to ensure complete understanding.\n\n    - **Create a Detailed Plan:** Develop a step-by-step plan that addresses every aspect of the user's requirements. Validate this plan before execution.\n\n    - **Utilize Advanced Planning Structures:** Do not limit yourself to linear or sequential plans. Employ loops for repetitive tasks, branches for conditional logic, and other programming constructs to handle complex tasks and decision-making processes.\n\n    - **Follow Instructions Precisely:** Execute each step exactly as described, without omitting or altering any part of the instructions.\n\n    - **Be Thorough:*

# Tool Call

In [ ]:
if llm_response.tool_calls is None or llm_response.tool_calls[0]["name"] != "filter_artists":
    raise ValueError("should be tool message calling 'filter_artists'")

In [35]:
tool_response = tool_node.invoke({"messages": messages})
for tool_message in  tool_response["messages"]:
    tool_message.pretty_print()

================================= Tool Message =================================
Name: tavily_search_results_json

[{"url": "https://www.businessinsider.com/best-most-important-artists-of-the-decade-2010s?op=1", "content": "Despite all her early success, Robyn's ascent to icon status didn't truly begin until she broke out of the major label mold. ... The pop star triumphantly returned as an independent artist in 2010"}, {"url": "https://www.ranker.com/list/top-2010s-artists/jovaughnbrown", "content": "Vote up the artists based only on their music from 2010 to 2019. From Kanye West and Taylor Swift to Bruno Mars and Janelle Monáe, we're ranking the best artists of the decade. This list of the top 2010s artists includes some of the most popular musicians , bands, and singers in pop, rap, country, EDM, rock, R&B, and more."}, {"url": "https://top40weekly.com/top-100-artists-of-the-10s/", "content": "The title of best-selling artist of the 2010s is often attributed to Taylor Swift, whose s

In [36]:
chat_prompt_template += tool_response["messages"]
messages = chat_prompt_template.format_messages()
messages

[SystemMessage(content="\n    You are an AI language assistant designed to execute tasks with precision and attention to detail. Your primary objective is to follow the user's instructions thoroughly and exactly as specified, leaving no detail unaddressed.\n\n    Guidelines:\n\n    - **Carefully Read Instructions:** Before starting any task, read all user instructions thoroughly to ensure complete understanding.\n\n    - **Create a Detailed Plan:** Develop a step-by-step plan that addresses every aspect of the user's requirements. Validate this plan before execution.\n\n    - **Utilize Advanced Planning Structures:** Do not limit yourself to linear or sequential plans. Employ loops for repetitive tasks, branches for conditional logic, and other programming constructs to handle complex tasks and decision-making processes.\n\n    - **Follow Instructions Precisely:** Execute each step exactly as described, without omitting or altering any part of the instructions.\n\n    - **Be Thorough:*

# Send Tool Result to LLM

In [37]:
llm_response = llm_with_tools.invoke(messages)
llm_response.pretty_print()

2024-11-26 10:16:46,558 - INFO - HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"


================================== Ai Message ==================================

To ensure our curated playlist features only artists that achieved success post-2010, I'll check each artist's career timeline to ensure compliance with Rule 3. Moving forward, I'll proceed to find the top tracks from the newly validated artist list and organize them properly. 

I'm proceeding in parallel with the tasks to identify any possible constraint using artist data and verifying their timeline. After that, I'll proceed with finding top tracks. Lastly, I will arrange the potential tracklist to ensure smooth transitions for a better listening experience.
Tool Calls:
  find_top_tracks (call_J3Hlw8B7lWISYmCnauK46NCA)
 Call ID: call_J3Hlw8B7lWISYmCnauK46NCA
  Args:
    artists: ['01aC2ikO4Xgb2LUpf9JfKp', '0YC18PBm9HcV71BdOT9hBj', '3lzTSpBz7pJHWQU5i3zaP1', '1SH6uqCGEoVR6REHLbZbHj', '6k8jtB1ZrdRwu1doZjHpO4', '13SknHTBb5dgeL2OEucwq4', '4cSlsN9N2g8O0Lwb7rDPvI', '0C0XlULifJtAgn6ZNCW2eu', '7C82Bw5AiySQQHfwDv

In [38]:
chat_prompt_template += llm_response
messages = chat_prompt_template.format_messages()
messages

[SystemMessage(content="\n    You are an AI language assistant designed to execute tasks with precision and attention to detail. Your primary objective is to follow the user's instructions thoroughly and exactly as specified, leaving no detail unaddressed.\n\n    Guidelines:\n\n    - **Carefully Read Instructions:** Before starting any task, read all user instructions thoroughly to ensure complete understanding.\n\n    - **Create a Detailed Plan:** Develop a step-by-step plan that addresses every aspect of the user's requirements. Validate this plan before execution.\n\n    - **Utilize Advanced Planning Structures:** Do not limit yourself to linear or sequential plans. Employ loops for repetitive tasks, branches for conditional logic, and other programming constructs to handle complex tasks and decision-making processes.\n\n    - **Follow Instructions Precisely:** Execute each step exactly as described, without omitting or altering any part of the instructions.\n\n    - **Be Thorough:*

In [ ]:
if llm_response.tool_calls is None or llm_response.tool_calls[0]["name"] != "find_top_tracks":
    raise ValueError("should be tool message calling 'find_top_tracks'")

# Tool Call

In [39]:
tool_response = tool_node.invoke({"messages": messages})
for tool_message in  tool_response["messages"]:
    tool_message.pretty_print()

2024-11-26 10:17:31,492 - ERROR - HTTP Error for GET to https://api.spotify.com/v1/artists/0YC18PBm9HcV71BdOT9hBj/top-tracks with Params: {'country': 'US'} returned 404 due to Resource not found
2024-11-26 10:17:31,495 - ERROR - HTTP Error for GET to https://api.spotify.com/v1/artists/0YC18PBm9HcV71BdOT9hBj/top-tracks with Params: {'country': 'US'} returned 404 due to Resource not found
2024-11-26 10:17:31,580 - ERROR - HTTP Error for GET to https://api.spotify.com/v1/artists/6k8jtB1ZrdRwu1doZjHpO4/top-tracks with Params: {'country': 'US'} returned 404 due to Resource not found
2024-11-26 10:17:31,620 - ERROR - HTTP Error for GET to https://api.spotify.com/v1/artists/3lzTSpBz7pJHWQU5i3zaP1/top-tracks with Params: {'country': 'US'} returned 404 due to Resource not found
2024-11-26 10:17:31,665 - ERROR - HTTP Error for GET to https://api.spotify.com/v1/artists/1SH6uqCGEoVR6REHLbZbHj/top-tracks with Params: {'country': 'US'} returned 404 due to Resource not found
2024-11-26 10:17:31,690 -

Unexpected error for artist 0YC18PBm9HcV71BdOT9hBj: http status: 404, code:-1 - https://api.spotify.com/v1/artists/0YC18PBm9HcV71BdOT9hBj/top-tracks?country=US:
 Resource not found, reason: None
Unexpected error for artist 0YC18PBm9HcV71BdOT9hBj: http status: 404, code:-1 - https://api.spotify.com/v1/artists/0YC18PBm9HcV71BdOT9hBj/top-tracks?country=US:
 Resource not found, reason: None
Unexpected error for artist 6k8jtB1ZrdRwu1doZjHpO4: http status: 404, code:-1 - https://api.spotify.com/v1/artists/6k8jtB1ZrdRwu1doZjHpO4/top-tracks?country=US:
 Resource not found, reason: None
Unexpected error for artist 3lzTSpBz7pJHWQU5i3zaP1: http status: 404, code:-1 - https://api.spotify.com/v1/artists/3lzTSpBz7pJHWQU5i3zaP1/top-tracks?country=US:
 Resource not found, reason: None
Unexpected error for artist 1SH6uqCGEoVR6REHLbZbHj: http status: 404, code:-1 - https://api.spotify.com/v1/artists/1SH6uqCGEoVR6REHLbZbHj/top-tracks?country=US:
 Resource not found, reason: None


2024-11-26 10:17:31,746 - ERROR - HTTP Error for GET to https://api.spotify.com/v1/artists/2FwbpF2r8VeUh3n48hAEkH/top-tracks with Params: {'country': 'US'} returned 404 due to Resource not found
2024-11-26 10:17:31,760 - ERROR - HTTP Error for GET to https://api.spotify.com/v1/artists/6k8jtB1ZrdRwu1doZjHpO4/top-tracks with Params: {'country': 'US'} returned 404 due to Resource not found
2024-11-26 10:17:31,838 - ERROR - HTTP Error for GET to https://api.spotify.com/v1/artists/13SknHTBb5dgeL2OEucwq4/top-tracks with Params: {'country': 'US'} returned 404 due to Resource not found


Unexpected error for artist 1SH6uqCGEoVR6REHLbZbHj: http status: 404, code:-1 - https://api.spotify.com/v1/artists/1SH6uqCGEoVR6REHLbZbHj/top-tracks?country=US:
 Resource not found, reason: None
Unexpected error for artist 2FwbpF2r8VeUh3n48hAEkH: http status: 404, code:-1 - https://api.spotify.com/v1/artists/2FwbpF2r8VeUh3n48hAEkH/top-tracks?country=US:
 Resource not found, reason: None
Unexpected error for artist 6k8jtB1ZrdRwu1doZjHpO4: http status: 404, code:-1 - https://api.spotify.com/v1/artists/6k8jtB1ZrdRwu1doZjHpO4/top-tracks?country=US:
 Resource not found, reason: None
Unexpected error for artist 13SknHTBb5dgeL2OEucwq4: http status: 404, code:-1 - https://api.spotify.com/v1/artists/13SknHTBb5dgeL2OEucwq4/top-tracks?country=US:
 Resource not found, reason: None


2024-11-26 10:17:31,916 - ERROR - HTTP Error for GET to https://api.spotify.com/v1/artists/4cSlsN9N2g8O0Lwb7rDPvI/top-tracks with Params: {'country': 'US'} returned 404 due to Resource not found


Unexpected error for artist 4cSlsN9N2g8O0Lwb7rDPvI: http status: 404, code:-1 - https://api.spotify.com/v1/artists/4cSlsN9N2g8O0Lwb7rDPvI/top-tracks?country=US:
 Resource not found, reason: None


2024-11-26 10:17:32,126 - ERROR - HTTP Error for GET to https://api.spotify.com/v1/artists/7C82Bw5AiySQQHfwDvcP9e/top-tracks with Params: {'country': 'US'} returned 404 due to Resource not found
2024-11-26 10:17:32,197 - ERROR - HTTP Error for GET to https://api.spotify.com/v1/artists/5I4eibDkC6kQps3o8qr3Ef/top-tracks with Params: {'country': 'US'} returned 404 due to Resource not found


Unexpected error for artist 7C82Bw5AiySQQHfwDvcP9e: http status: 404, code:-1 - https://api.spotify.com/v1/artists/7C82Bw5AiySQQHfwDvcP9e/top-tracks?country=US:
 Resource not found, reason: None
Unexpected error for artist 5I4eibDkC6kQps3o8qr3Ef: http status: 404, code:-1 - https://api.spotify.com/v1/artists/5I4eibDkC6kQps3o8qr3Ef/top-tracks?country=US:
 Resource not found, reason: None


2024-11-26 10:17:32,670 - ERROR - HTTP Error for GET to https://api.spotify.com/v1/artists/1eyzqe2QqGZUmfcPZtrIyt/top-tracks with Params: {'country': 'US'} returned 404 due to Resource not found


Unexpected error for artist 1eyzqe2QqGZUmfcPZtrIyt: http status: 404, code:-1 - https://api.spotify.com/v1/artists/1eyzqe2QqGZUmfcPZtrIyt/top-tracks?country=US:
 Resource not found, reason: None
================================= Tool Message =================================
Name: find_top_tracks

["45HAjqRWiNv6mMPw4NvZrU", "4rVW6XqAsSaf5vOwc8FREW", "7aO35V27YDi4hKOL9odSya", "4iu49FeQQGiUh2Dn1A8qCl", "59oXRNRnmmTbwgkZkV7l4g", "10V1dKQyQlL9nI7KpPPeBp", "2CU9pGd7lq4fSHiFwjs842", "2HF9OydUs28eTuiVUjQYdT", "2mdxGlwrhtkuxgzbH7LOIh", "4bGTNdEbmrDlvqYJKRKJxR", "003vvx7Niy0yvhvHt4a68B", "6PwjJ58I4t7Mae9xfZ9l9v", "70wYA8oYHoMzhRRkARoMhU", "1sTsuZTdANkiFd7T34H3nb", "5vollujufHY0jMZxx77VWr", "7cX4PJz1old9fyFI8RlfgW", "3KANrKOFYyAxfjQJHkgBdb", "5aWhs651KYM26HYM16kRdk", "2aZ2Co4NeQRsqWcU930zHT", "1A8SxnqRK3qabmuN2qxIpa", "1Es7AUAhQvapIcoh3qMKDL", "7CyPwkp0oE8Ro9Dd5CUDjW", "0VjIjW4GlUZAMYd2vXMi3b", "7MXVkk9YMctZqd1Srtv4MB", "2LBqCSwhJGcFQeTHMVGwy3", "0xGQTpN4ESETtl1Sp6rzd2", "7z7kvUQGwlC6iOl7vMuAr9"

In [40]:
chat_prompt_template += tool_response["messages"]
messages = chat_prompt_template.format_messages()
messages

[SystemMessage(content="\n    You are an AI language assistant designed to execute tasks with precision and attention to detail. Your primary objective is to follow the user's instructions thoroughly and exactly as specified, leaving no detail unaddressed.\n\n    Guidelines:\n\n    - **Carefully Read Instructions:** Before starting any task, read all user instructions thoroughly to ensure complete understanding.\n\n    - **Create a Detailed Plan:** Develop a step-by-step plan that addresses every aspect of the user's requirements. Validate this plan before execution.\n\n    - **Utilize Advanced Planning Structures:** Do not limit yourself to linear or sequential plans. Employ loops for repetitive tasks, branches for conditional logic, and other programming constructs to handle complex tasks and decision-making processes.\n\n    - **Follow Instructions Precisely:** Execute each step exactly as described, without omitting or altering any part of the instructions.\n\n    - **Be Thorough:*

# Send Tool Result to LLM

In [41]:
llm_response = llm_with_tools.invoke(messages)
llm_response.pretty_print()

2024-11-26 10:18:44,136 - INFO - HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"


================================== Ai Message ==================================
Tool Calls:
  get_audio_features (call_E8zCXxqId3CUQpgAXxGnVb4E)
 Call ID: call_E8zCXxqId3CUQpgAXxGnVb4E
  Args:
    tracks: ['45HAjqRWiNv6mMPw4NvZrU', '4rVW6XqAsSaf5vOwc8FREW', '7aO35V27YDi4hKOL9odSya', '4iu49FeQQGiUh2Dn1A8qCl', '59oXRNRnmmTbwgkZkV7l4g', '10V1dKQyQlL9nI7KpPPeBp', '2CU9pGd7lq4fSHiFwjs842', '2HF9OydUs28eTuiVUjQYdT', '2mdxGlwrhtkuxgzbH7LOIh', '4bGTNdEbmrDlvqYJKRKJxR', '003vvx7Niy0yvhvHt4a68B', '6PwjJ58I4t7Mae9xfZ9l9v', '70wYA8oYHoMzhRRkARoMhU', '1sTsuZTdANkiFd7T34H3nb', '5vollujufHY0jMZxx77VWr', '7cX4PJz1old9fyFI8RlfgW', '3KANrKOFYyAxfjQJHkgBdb', '5aWhs651KYM26HYM16kRdk', '2aZ2Co4NeQRsqWcU930zHT', '1A8SxnqRK3qabmuN2qxIpa', '1Es7AUAhQvapIcoh3qMKDL', '7CyPwkp0oE8Ro9Dd5CUDjW', '0VjIjW4GlUZAMYd2vXMi3b', '7MXVkk9YMctZqd1Srtv4MB', '2LBqCSwhJGcFQeTHMVGwy3', '0xGQTpN4ESETtl1Sp6rzd2', '7z7kvUQGwlC6iOl7vMuAr9', '5QO79kh1waicV47BqGRL3g', '7fBv7CLKzipRk6EC6TWHOB', '5gDWsRxpJ2lZAffh5p7K0w', '4okLKeB83VLZ

In [42]:
chat_prompt_template += llm_response
messages = chat_prompt_template.format_messages()
messages

[SystemMessage(content="\n    You are an AI language assistant designed to execute tasks with precision and attention to detail. Your primary objective is to follow the user's instructions thoroughly and exactly as specified, leaving no detail unaddressed.\n\n    Guidelines:\n\n    - **Carefully Read Instructions:** Before starting any task, read all user instructions thoroughly to ensure complete understanding.\n\n    - **Create a Detailed Plan:** Develop a step-by-step plan that addresses every aspect of the user's requirements. Validate this plan before execution.\n\n    - **Utilize Advanced Planning Structures:** Do not limit yourself to linear or sequential plans. Employ loops for repetitive tasks, branches for conditional logic, and other programming constructs to handle complex tasks and decision-making processes.\n\n    - **Follow Instructions Precisely:** Execute each step exactly as described, without omitting or altering any part of the instructions.\n\n    - **Be Thorough:*

# Tool Call

In [43]:
tool_response = tool_node.invoke({"messages": messages})
for tool_message in  tool_response["messages"]:
    tool_message.pretty_print()

================================= Tool Message =================================
Name: get_audio_features

[{"danceability": 0.447, "energy": 0.788, "key": 2, "loudness": -4.994, "mode": 0, "speechiness": 0.0464, "acousticness": 0.00257, "instrumentalness": 1.68e-05, "liveness": 0.0744, "valence": 0.505, "tempo": 80.04, "type": "audio_features", "id": "45HAjqRWiNv6mMPw4NvZrU", "uri": "spotify:track:45HAjqRWiNv6mMPw4NvZrU", "track_href": "https://api.spotify.com/v1/tracks/45HAjqRWiNv6mMPw4NvZrU", "analysis_url": "https://api.spotify.com/v1/audio-analysis/45HAjqRWiNv6mMPw4NvZrU", "duration_ms": 193714, "time_signature": 4}, {"danceability": 0.557, "energy": 0.585, "key": 8, "loudness": -6.201, "mode": 1, "speechiness": 0.0431, "acousticness": 0.036, "instrumentalness": 0, "liveness": 0.176, "valence": 0.305, "tempo": 63.392, "type": "audio_features", "id": "4rVW6XqAsSaf5vOwc8FREW", "uri": "spotify:track:4rVW6XqAsSaf5vOwc8FREW", "track_href": "https://api.spotify.com/v1/tracks/4rVW6XqAsSa

In [ ]:
tool_message

In [44]:
chat_prompt_template += tool_response["messages"]
messages = chat_prompt_template.format_messages()
messages

[SystemMessage(content="\n    You are an AI language assistant designed to execute tasks with precision and attention to detail. Your primary objective is to follow the user's instructions thoroughly and exactly as specified, leaving no detail unaddressed.\n\n    Guidelines:\n\n    - **Carefully Read Instructions:** Before starting any task, read all user instructions thoroughly to ensure complete understanding.\n\n    - **Create a Detailed Plan:** Develop a step-by-step plan that addresses every aspect of the user's requirements. Validate this plan before execution.\n\n    - **Utilize Advanced Planning Structures:** Do not limit yourself to linear or sequential plans. Employ loops for repetitive tasks, branches for conditional logic, and other programming constructs to handle complex tasks and decision-making processes.\n\n    - **Follow Instructions Precisely:** Execute each step exactly as described, without omitting or altering any part of the instructions.\n\n    - **Be Thorough:*

# Send Tool Result to LLM

In [45]:
llm_response = llm_with_tools.invoke(messages)
llm_response.pretty_print()

2024-11-26 10:19:07,197 - INFO - HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"


================================== Ai Message ==================================
Tool Calls:
  create_spotify_playlist (call_8taVEbOBzPHVSBR3RaCsicps)
 Call ID: call_8taVEbOBzPHVSBR3RaCsicps
  Args:
    name: Curated Rock and Blues - Post 2010 Vibes
    description: A selection of tracks mimicking the vibe and feel of 'New Rock and Blues' with artists who came to prominence after 2010.
